# **EDA Mental Health - First Submission**

# **Set-up**

In [73]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
import plotly.io as pio
import plotly.graph_objects as go
from plotly.subplots import make_subplots
pd.options.plotting.backend = "plotly"
pio.templates.default = "simple_white"
warnings.filterwarnings('ignore')

# Import ML
import optuna
from optuna.visualization import plot_param_importances, plot_contour
from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.model_selection import cross_validate
from sklearn.metrics import accuracy_score, roc_auc_score, matthews_corrcoef
import joblib
from catboost import CatBoostClassifier, Pool


In [2]:
train = pd.read_csv('Data/train.csv')
test = pd.read_csv('Data/test.csv')
submission = pd.read_csv('Data/sample_submission.csv')
original = pd.read_csv('Data/final_depression_dataset_1.csv')

# **Custom Functions**

In [85]:
def train_bagged_model(
    X, 
    y, 
    model_params, 
    n_folds=5, 
    cat_features=None, 
    random_state=42
):
    """
    Train a bagged model using K-fold cross-validation approach.
    
    Args:
        X: Training features
        y: Target variable
        model_params: Parameters for CatBoostClassifier
        n_folds: Number of folds for cross-validation
        cat_features: List of categorical feature names
        random_state: Random seed
    
    Returns:
        oof_predictions: Out-of-fold predictions for training data
        models: List of trained models
    """
    # Initialize arrays for predictions
    oof_predictions = np.zeros(len(X))
    models = []
    
    # Initialize lists to store CV scores for each fold
    fold_mcc_scores = []
    fold_acc_scores = []
    fold_auc_scores = []
    
    # Create K-fold splits
    kf = StratifiedKFold(n_splits=n_folds, shuffle=True, random_state=random_state)
    
    # Train K models
    for fold, (train_idx, val_idx) in enumerate(kf.split(X, y)):
        print(f"Training fold {fold + 1}/{n_folds}")
        
        # Prepare training data
        train_data = Pool(
            X.iloc[train_idx],
            y.iloc[train_idx],
            cat_features=cat_features
        )
        val_data = Pool(
            X.iloc[val_idx],
            y.iloc[val_idx],
            cat_features=cat_features
        )
        
        # Initialize and train model
        model = CatBoostClassifier(
            **model_params,
            random_state=random_state + fold
        )
        
        model.fit(
            train_data,
            eval_set=val_data,
            early_stopping_rounds=50,
            verbose=0
        )
        
        # Generate OOF predictions for this fold
        fold_preds = model.predict_proba(X.iloc[val_idx])[:, 1]
        oof_predictions[val_idx] = fold_preds
        
        # Calculate and store CV scores for this fold
        fold_mcc = matthews_corrcoef(y.iloc[val_idx], (fold_preds > 0.5).astype(int))
        fold_acc = accuracy_score(y.iloc[val_idx], (fold_preds > 0.5).astype(int))
        fold_auc = roc_auc_score(y.iloc[val_idx], fold_preds)
        
        fold_mcc_scores.append(fold_mcc)
        fold_acc_scores.append(fold_acc)
        fold_auc_scores.append(fold_auc)
        
        # Save model
        models.append(model)

    # Calculate mean and std of fold scores
    mean_mcc = np.mean(fold_mcc_scores)
    std_mcc = np.std(fold_mcc_scores)
    mean_acc = np.mean(fold_acc_scores)
    std_acc = np.std(fold_acc_scores)
    mean_auc = np.mean(fold_auc_scores)
    std_auc = np.std(fold_auc_scores)

    print(f"\nCross-validation Scores (Mean ± Std):")
    print(f"AUC Score: {mean_auc:.4f} ± {std_auc:.4f}")
    print(f"MCC Score: {mean_mcc:.4f} ± {std_mcc:.4f}")
    print(f"Accuracy Score: {mean_acc:.4f} ± {std_acc:.4f}")

    return oof_predictions, models

# **Data Cleaning**

The data is very noisy and uncleaned. We need to clean it before using it.

In [3]:
train = train.set_index('id').drop(columns=['Name'])
test = test.set_index('id').drop(columns=['Name'])
original = original.drop(columns=['Name'])
train.shape, test.shape, submission.shape, original.shape

((140700, 18), (93800, 17), (93800, 2), (2556, 18))

In [4]:
# Renaming columns for consistency 
train.columns = train.columns.str.lower()
test.columns = test.columns.str.lower()
train.columns = ['is_female', 'age', 'city', 'is_student',
       'profession', 'academic_pressure', 'work_pressure', 'cgpa',
       'study_satisfaction', 'job_satisfaction', 'sleep_duration',
       'dietary_habits', 'degree', 'suicidal_thoughts',
       'work_study_hours', 'financial_stress',
       'family_history', 'depression']
test.columns = ['is_female', 'age', 'city', 'is_student',
       'profession', 'academic_pressure', 'work_pressure', 'cgpa',
       'study_satisfaction', 'job_satisfaction', 'sleep_duration',
       'dietary_habits', 'degree', 'suicidal_thoughts',
       'work_study_hours', 'financial_stress',
       'family_history']
original.columns = ['is_female', 'age', 'city', 'is_student', 'profession',
                    'academic_pressure', 'work_pressure', 'cgpa',
                    'study_satisfaction', 'job_satisfaction', 'sleep_duration',
                    'dietary_habits', 'degree', 'suicidal_thoughts',
                    'work_study_hours', 'financial_stress', 'family_history',
                    'depression']

# Convert binary features to 0/1
train['is_female'] = np.where(train['is_female'] == 'Female', 1, 0)
test['is_female'] = np.where(test['is_female'] == 'Female', 1, 0)
original['is_female'] = np.where(original['is_female'] == 'Female', 1, 0)
train['is_student'] = np.where(train['is_student'] == 'Student', 1, 0)
test['is_student'] = np.where(test['is_student'] == 'Student', 1, 0)
original['is_student'] = np.where(original['is_student'] == 'Student', 1, 0)
train['suicidal_thoughts'] = np.where(train['suicidal_thoughts'] == 'Yes', 1, 0)
test['suicidal_thoughts'] = np.where(test['suicidal_thoughts'] == 'Yes', 1, 0)
original['suicidal_thoughts'] = np.where(original['suicidal_thoughts'] == 'Yes', 1, 0)
train['family_history'] = np.where(train['family_history'] == 'Yes', 1, 0)
test['family_history'] = np.where(test['family_history'] == 'Yes', 1, 0)
original['family_history'] = np.where(original['family_history'] == 'Yes', 1, 0)
original['depression'] = np.where(original['depression'] == 'Yes', 1, 0)


In [5]:
# Convert numerical features to integer
to_integer = ['is_female', 'age', 'is_student', 'suicidal_thoughts', 'family_history', 'depression']

for col in to_integer:
    print(f"Converting {col} to integer")
    train[col] = train[col].astype(np.int32)
    original[col] = original[col].astype(np.int32)
    if col != 'depression':
        test[col] = test[col].astype(np.int32)
  
# Convert float64 columns to float32 to reduce memory usage
float_cols = train.select_dtypes(include=['float64']).columns
for col in float_cols:
    print(f"Converting {col} from {train[col].dtype} to float32")
    train[col] = train[col].astype(np.float32)
    test[col] = test[col].astype(np.float32)
    original[col] = original[col].astype(np.float32)


Converting is_female to integer
Converting age to integer
Converting is_student to integer
Converting suicidal_thoughts to integer
Converting family_history to integer
Converting depression to integer
Converting academic_pressure from float64 to float32
Converting work_pressure from float64 to float32
Converting cgpa from float64 to float32
Converting study_satisfaction from float64 to float32
Converting job_satisfaction from float64 to float32
Converting work_study_hours from float64 to float32
Converting financial_stress from float64 to float32


In [6]:
# Joining train and original
# Create sequential IDs for original dataset starting after last train ID
last_train_id = train.index.max()
original.index = pd.RangeIndex(start=last_train_id + 1, 
                             stop=last_train_id + len(original) + 1)
original.index.name = 'id'
train['is_original'] = 0
original['is_original'] = 1
train_or = pd.concat([train, original])
train_or

is_female  age           city  is_student        profession  \
id                                                                    
0               1   49       Ludhiana           0              Chef   
1               0   26       Varanasi           0           Teacher   
2               0   33  Visakhapatnam           1               NaN   
3               0   22         Mumbai           0           Teacher   
4               1   30         Kanpur           0  Business Analyst   
...           ...  ...            ...         ...               ...   
143251          0   25      Bangalore           0        Consultant   
143252          1   23           Pune           0           Teacher   
143253          1   24       Srinagar           0        HR Manager   
143254          1   56      Bangalore           0  Business Analyst   
143255          0   18          Surat           1               NaN   

        academic_pressure  work_pressure  cgpa  study_satisfaction  \
id                                                                   
0                     NaN            5.0   NaN                 NaN   
1                     NaN            4.0   NaN                 NaN   
2                     5.0            NaN  8.97                 2.0   
3                     NaN            5.0   NaN                 NaN   
4                     NaN            1.0   NaN                 NaN   
...                   ...            ...   ...                 ...   
143251                NaN            1.0   NaN                 NaN   
143252                NaN            3.0   NaN                 NaN   
143253                NaN            1.0   NaN                 NaN   
143254                NaN            2.0   NaN                 NaN   
143255                5.0            NaN  6.70                 3.0   

        job_satisfaction     sleep_duration dietary_habits    degree  \
id                                                                     
0                    2.0  More than 8 hours        Healthy       BHM   
1                    3.0  Less than 5 hours      Unhealthy       LLB   
2                    NaN          5-6 hours        Healthy   B.Pharm   
3                    1.0  Less than 5 hours       Moderate       BBA   
4                    1.0          5-6 hours      Unhealthy       BBA   
...                  ...                ...            ...       ...   
143251               5.0          5-6 hours        Healthy       BBA   
143252               1.0  Less than 5 hours       Moderate        MA   
143253               4.0  Less than 5 hours       Moderate        BA   
143254               3.0          7-8 hours        Healthy       BBA   
143255               NaN  More than 8 hours      Unhealthy  Class 12   

        suicidal_thoughts  work_study_hours  financial_stress  family_history  \
id                                                                              
0                       0               1.0               2.0               0   
1                       1               7.0               3.0               0   
2                       1               3.0               1.0               0   
3                       1              10.0               1.0               1   
4                       1               9.0               4.0               1   
...                   ...               ...               ...             ...   
143251                  1              12.0               3.0               1   
143252                  1               8.0               3.0               0   
143253                  1               4.0               4.0               0   
143254                  0               4.0               5.0               1   
143255                  0               6.0               2.0               1   

        depression  is_original  
id                               
0                0            0  
1                1            0  
2                1            0  
3           

## **Comparing train and original**

### **Binary Features**

In [7]:
binary_features = ['is_female', 'is_student', 'suicidal_thoughts', 'family_history']
fig = make_subplots(rows=2, cols=2, subplot_titles=binary_features)

# Define consistent colors for Train and Original
train_color = '#1f77b4'  # Blue
original_color = '#ff7f0e'  # Orange

for i, feat in enumerate(binary_features):
    pcts = train_or.groupby('is_original')[feat].value_counts(normalize=True, dropna=False).unstack().T
    fig.add_trace(go.Bar(x=[0,1], y=pcts[0], name='Train', marker_color=train_color, showlegend=i==0), 
                 row=i//2+1, col=i%2+1)
    fig.add_trace(go.Bar(x=[0,1], y=pcts[1], name='Original', marker_color=original_color, showlegend=i==0), 
                 row=i//2+1, col=i%2+1)

fig.update_layout(height=600, width=1000, barmode='group')
fig.show()

They are basically the same. No need to do anything here. 

### **Ordered Features**

In [8]:
ordered_features = ['academic_pressure', 'work_pressure', 'study_satisfaction', 'job_satisfaction', 'financial_stress']
fig = make_subplots(rows=3, cols=2, subplot_titles=ordered_features)

# Define consistent colors for Train and Original
train_color = '#1f77b4'  # Blue
original_color = '#ff7f0e'  # Orange

for i, feat in enumerate(ordered_features):
    pcts = train_or.groupby('is_original')[feat].value_counts(normalize=True).unstack().T
    
    fig.add_trace(go.Bar(x=pcts.index, y=pcts[0], name='Train', marker_color=train_color, showlegend=i==0), 
                 row=i//2+1, col=i%2+1)
    fig.add_trace(go.Bar(x=pcts.index, y=pcts[1], name='Original', marker_color=original_color, showlegend=i==0), 
                 row=i//2+1, col=i%2+1)

fig.update_layout(height=800, width=1000, barmode='group')
fig.show()

There is no much difference between the two datasets in terms of the ordered features. 

### **Numerical Features**

In [9]:
numerical_features = ['age', 'cgpa']
fig = make_subplots(rows=1, cols=2, subplot_titles=numerical_features)

# Define consistent colors for Train and Original
train_color = '#1f77b4'  # Blue
original_color = '#ff7f0e'  # Orange

for i, feat in enumerate(numerical_features):
    fig.add_trace(go.Box(y=train_or[train_or['is_original']==0][feat], 
                        name='Train',
                        marker_color=train_color,
                        showlegend=i==0),
                 row=1, col=i+1)
    fig.add_trace(go.Box(y=train_or[train_or['is_original']==1][feat],
                        name='Original', 
                        marker_color=original_color,
                        showlegend=i==0),
                 row=1, col=i+1)

fig.update_layout(height=400, width=1000, boxmode='group')
fig.show()


Almost identical distributions. 

### **Categorical Features**

In [10]:
feature = 'sleep_duration'

# Calculate proportions for each dataset
train_props = (train_or[train_or['is_original']==0][feature]
              .value_counts(normalize=True)
              .mul(100)
              .round(2))

orig_props = (train_or[train_or['is_original']==1][feature]
             .value_counts(normalize=True)
             .mul(100)
             .round(2))

# Print comparisons
print("Matching categories:")
for cat in sorted(set(train_props.index) & set(orig_props.index)):
    print(f"{cat:<20} Train: {train_props[cat]:>5}%  Original: {orig_props[cat]:>5}%")

print("\nOnly in Train:")
for cat in sorted(set(train_props.index) - set(orig_props.index)):
    print(f"{cat:<20} Train: {train_props[cat]:>5}%")

print("\nOnly in Original:")
for cat in sorted(set(orig_props.index) - set(train_props.index)):
    print(f"{cat:<20} Original: {orig_props[cat]:>5}%")

Matching categories:
5-6 hours            Train: 22.84%  Original: 24.57%
7-8 hours            Train: 26.28%  Original: 25.74%
Less than 5 hours    Train: 27.57%  Original: 25.35%
More than 8 hours    Train: 23.26%  Original: 24.33%

Only in Train:
1-2 hours            Train:   0.0%
1-3 hours            Train:   0.0%
1-6 hours            Train:   0.0%
10-11 hours          Train:   0.0%
10-6 hours           Train:   0.0%
2-3 hours            Train:   0.0%
3-4 hours            Train:  0.01%
3-6 hours            Train:   0.0%
35-36 hours          Train:   0.0%
4-5 hours            Train:   0.0%
4-6 hours            Train:   0.0%
40-45 hours          Train:   0.0%
45                   Train:   0.0%
45-48 hours          Train:   0.0%
49 hours             Train:   0.0%
55-66 hours          Train:   0.0%
6-7 hours            Train:  0.01%
6-8 hours            Train:   0.0%
8 hours              Train:   0.0%
8-9 hours            Train:   0.0%
9-11 hours           Train:   0.0%
9-5             

As expected with these generated datasets, there are artifacts in the categorical features. We will convert to NA all the categories that are not in the original dataset. 

In [11]:
categorical_features = ['profession', 'city', 'degree', 'dietary_habits', 'sleep_duration']

for col in categorical_features:
    # Get valid categories from original dataset
    valid_cats = set(train_or[train_or['is_original']==1][col].dropna().unique())
    
    # Convert non-matching categories to NA
    train_or.loc[~train_or[col].isin(valid_cats), col] = np.nan
    test.loc[~test[col].isin(valid_cats), col] = np.nan

# **Missing Values**

In [12]:
# Calculate missing values and percentages
missing = pd.DataFrame({
    'Train': train_or.isna().sum(),
    'Train_%': (train_or.isna().mean() * 100).round(2),
    'Test': test.isna().sum(),
    'Test_%': (test.isna().mean() * 100).round(2)
}).query("Train > 0 or Test > 0").sort_values('Train_%', ascending=False)

# Display only features with missing values
print(missing)

# Visualize using Plotly
fig = go.Figure()
fig.add_trace(go.Bar(name='Train', x=missing.index, y=missing['Train_%']))
fig.add_trace(go.Bar(name='Test', x=missing.index, y=missing['Test_%']))

fig.update_layout(
    title='Missing Values Percentage by Dataset',
    barmode='group',
    height=600,
    width=1000,
    xaxis_tickangle=-45
)
fig.show()

                     Train  Train_%     Test  Test_%
academic_pressure   114857    80.18  75033.0   79.99
cgpa                114856    80.18  75034.0   79.99
study_satisfaction  114857    80.18  75033.0   79.99
profession           37353    26.07  24676.0   26.31
work_pressure        28420    19.84  18778.0   20.02
job_satisfaction     28412    19.83  18774.0   20.01
degree                 116     0.08     86.0    0.09
city                    98     0.07     50.0    0.05
sleep_duration          79     0.06     54.0    0.06
dietary_habits          27     0.02     30.0    0.03
financial_stress         4     0.00      0.0    0.00


- `academic_pressure`, `cpga`, `study_satisfaction` have almost 80% of missing values and this is simetric in both train and test.
- `profession`, `work_pressure`, `job_satisfaction` have between 20-30% of missing values in both datasets.
- The rest of the features with NA is not relevant for the problem. 
- **Non-respondents can be a feature by itself.**



# **Relationship with the target**

In [13]:
# Lets see the relationship between the features and the target. 
# Separate numerical and categorical features
num_features = train_or.select_dtypes(include=['int32', 'float32']).columns.tolist()
cat_features = train_or.select_dtypes(include=['object', 'string']).columns.tolist()

# Remove target and is_original from features
num_features = [f for f in num_features if f not in ['depression', 'is_original']]
cat_features = [f for f in cat_features if f not in ['depression', 'is_original']]

In [14]:
# Remove target and is_original
features = [f for f in train_or.columns if f not in ['depression', 'is_original']]

# Calculate depression rate for each feature value
fig = make_subplots(rows=len(features)//3 + 1, cols=3, 
                    subplot_titles=features)

for i, feat in enumerate(features):
    # Calculate proportions
    props = (train_or.fillna({feat: -1 if original[feat].dtype.kind in 'biufc' else 'NA'})
            .groupby(feat)['depression']
            .agg(['count', 'mean'])
            .assign(pct=lambda x: x['mean'] * 100)
            .round(2)
            .sort_values('mean', ascending=False))
    
    # Add count as hover text
    hover_text = [f"Count: {c}" for c in props['count']]
    
    fig.add_trace(
        go.Bar(x=props.index, 
               y=props['pct'], 
               text=props['pct'].apply(lambda x: f"{x:.1f}%"),
               hovertext=hover_text,
               name=feat),
        row=i//3 + 1, col=i%3 + 1
    )

fig.update_layout(height=300*((len(features)//3) + 1), 
                 width=1000, 
                 showlegend=False,
                 title_text="Depression Rate by Feature Values")
fig.show()

The results are very interesting:

- Beign younger (age < 20), student increases significantly the probability of having depression. Students in particularly is a defining factor in this dataset.
- As expected, ordered features correlate with depression:
    - `academic_pressure`, `work_pressure`, `financial_stress`, `work_study_hours` as it increases, the probability of having depression increases.
    - `study_satisfaction`, `job_satisfaction` as it decreases, the probability of having depression increases.
- Having bad `dietary_habits` and `sleep_duration` decreases the probability of having depression.
- `Gender` and `family_history` do not show a strong correlation with depression. However, they may have interaction with other features.
- `Graphic Designer` is the top profession with high proportion of depression.
- `Hyderabad` is the top city with high proportion of depression. This could be biased because there are more students living there and also is an importante tech hub in India where there is high academic pressure.
- Having `suicidal_thoughts` is not a good sign, 31% of the people with suicidal thoughts have depression, whereas only 5% of the people without suicidal thoughts have depression.
- `Class 12` in India is a crucial year in a student's life because it is the year when students take very important exams that may determine their future. This may explain why there is a high proportion of depression in this group.
- **Missing Values** usually have a high proportion of depression in certain features like `work_pressure`, `financial_stress` because all of the NAs are practically students. Whereas, missing values in student related features like `academic_pressure`, `study_satisfaction` have low proportions of depression because there are not students. 

In [15]:
# Lets look at the relationship between CGPA and depression more closely
# Create CGPA buckets
train_or['cgpa_bucket'] = pd.cut(train_or['cgpa'], 
                                bins=[5, 6, 7, 8, 9, 10], 
                                labels=['5-6', '6-7', '7-8', '8-9', '9-10'])

# Calculate depression rate by bucket
props = (train_or.groupby('cgpa_bucket')['depression']
 .agg(['count', 'mean'])
 .assign(pct=lambda x: x['mean'] * 100)
 .round(2))

# Visualize
fig = go.Figure()
fig.add_trace(go.Bar(x=props.index, 
                     y=props['pct'],
                     text=props['pct'].apply(lambda x: f"{x:.1f}%"),
                     hovertext=[f"Count: {c}" for c in props['count']]))
fig.update_layout(title='Depression Rate by CGPA Range',
                 xaxis_title='CGPA Range',
                 yaxis_title='Depression Rate (%)',
                 width=800)
fig.show()

It seems that the higher the CGPA, the higher the proportion of having depression, but it is not a clear relationship. 

In [28]:
train_or.to_csv('Data/train_cleaned.csv', index=False)
test.to_csv('Data/test_cleaned.csv', index=False)
original.to_csv('Data/original_cleaned.csv', index=False)

# **Modeling**

I will try 2 approaches:
- A tuned catboost model
- A tuned bagged catboost model

The use of catboost is because of its superior capabilities in handling categorical features. 

In [20]:
features = [f for f in train_or.columns if f not in ['depression', 'is_original', 'cgpa_bucket']]
cat_features = ['city', 'profession', 'degree', 'dietary_habits', 'sleep_duration']

In [31]:
# Fill NaN in categorical features with 'Missing'
train_or_prep = train_or.copy()
test_prep = test.copy()

for feat in cat_features:
    train_or_prep[feat] = train_or_prep[feat].fillna('Missing')
    test_prep[feat] = test_prep[feat].fillna('Missing')


## **Optuna Tunning**

In [58]:
def objective(trial):
    bootstrap_type = trial.suggest_categorical('bootstrap_type', ['Bernoulli', 'Bayesian'])
    
    params = {
        'iterations': trial.suggest_int('iterations', 300, 5000),
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.1, log=True),
        'depth': trial.suggest_int('depth', 4, 10),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-8, 10.0, log=True),
        'bootstrap_type': bootstrap_type,
        'random_strength': trial.suggest_float('random_strength', 1e-8, 10.0, log=True),
        'min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 1, 2000),
        'scale_pos_weight': trial.suggest_float('scale_pos_weight', 1, 10),
        'eval_metric': 'AUC'  
    }
    
    if bootstrap_type == 'Bernoulli':
        params['subsample'] = trial.suggest_float('subsample', 0.5, 1.0)
    
    cv_aucs = []
    skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    
    for fold, (train_idx, val_idx) in enumerate(skf.split(train_or_prep, train_or_prep['depression'])):
        train_data = Pool(
            train_or_prep.iloc[train_idx][features],
            train_or_prep.iloc[train_idx]['depression'],
            cat_features=cat_features
        )
        val_data = Pool(
            train_or_prep.iloc[val_idx][features],
            train_or_prep.iloc[val_idx]['depression'],
            cat_features=cat_features
        )
        
        model = CatBoostClassifier(
            **params,
            random_state=42+fold,
            task_type='CPU',
            od_type='IncToDec',
            od_wait=20
        )
        model.fit(train_data, eval_set=val_data, early_stopping_rounds=100, verbose=0)
        
        # Calculate AUC on validation set
        val_preds = model.predict_proba(train_or_prep.iloc[val_idx][features])[:, 1]
        auc = roc_auc_score(train_or_prep.iloc[val_idx]['depression'], val_preds)
        cv_aucs.append(auc)
    
    return np.mean(cv_aucs)  # Optimize for AUC

In [59]:
# Run Optuna optimization
study = optuna.create_study(direction='maximize',     
                            storage="sqlite:///Data/optuna_M1_catboost_tuned.db",
                            load_if_exists=False)
study.optimize(objective, n_trials=50, n_jobs=-1)

[I 2024-11-11 07:57:56,110] A new study created in RDB with name: no-name-457b7bbe-91f4-436a-8626-cf38bc1c20b7
Training has stopped (degenerate solution on iteration 155, probably too small l2-regularization, try to increase it)
Training has stopped (degenerate solution on iteration 49, probably too small l2-regularization, try to increase it)
Training has stopped (degenerate solution on iteration 248, probably too small l2-regularization, try to increase it)
Training has stopped (degenerate solution on iteration 162, probably too small l2-regularization, try to increase it)
Training has stopped (degenerate solution on iteration 186, probably too small l2-regularization, try to increase it)
Training has stopped (degenerate solution on iteration 203, probably too small l2-regularization, try to increase it)
Training has stopped (degenerate solution on iteration 561, probably too small l2-regularization, try to increase it)
Training has stopped (degenerate solution on iteration 743, prob

In [61]:
# Get best parameters
best_params = study.best_params
best_score = study.best_value
print(f"Best parameters found: {best_params}")
print(f"with best Score: {best_score}")

Best parameters found: {'bootstrap_type': 'Bayesian', 'iterations': 2703, 'learning_rate': 0.02830784856467311, 'depth': 4, 'l2_leaf_reg': 0.12349929471360076, 'random_strength': 0.3959760669642191, 'min_data_in_leaf': 459, 'scale_pos_weight': 4.713833569834194}
with best Score: 0.9758207178301473


In [62]:
plot_param_importances(study)


In [63]:
trials_df = study.trials_dataframe()

# Lets see top 10% of the trials
top_sharpes = trials_df[trials_df['value'] >= trials_df['value'].quantile(0.90)]
top_sharpes.sort_values(by="value", ascending=False).head(5)

number     value             datetime_start          datetime_complete  \
34      34  0.975821 2024-11-11 09:59:57.492451 2024-11-11 10:21:36.579353   
37      37  0.975803 2024-11-11 10:06:56.297661 2024-11-11 10:27:04.012690   
23      23  0.975800 2024-11-11 08:21:06.618186 2024-11-11 08:38:58.112157   
40      40  0.975799 2024-11-11 10:16:43.118512 2024-11-11 10:36:06.047572   
42      42  0.975794 2024-11-11 10:19:23.323809 2024-11-11 10:28:48.553149   

                 duration params_bootstrap_type  params_depth  \
34 0 days 00:21:39.086902              Bayesian             4   
37 0 days 00:20:07.715029              Bayesian             4   
23 0 days 00:17:51.493971              Bayesian             4   
40 0 days 00:19:22.929060              Bayesian             4   
42 0 days 00:09:25.229340              Bayesian             4   

    params_iterations  params_l2_leaf_reg  params_learning_rate  \
34               2703            0.123499              0.028308   
37               2820            0.192054              0.023747   
23               2323            7.063295              0.035127   
40               3362            0.127427              0.024482   
42               3295            0.004291              0.055834   

    params_min_data_in_leaf  params_random_strength  params_scale_pos_weight  \
34                      459                0.395976                 4.713834   
37                      451                0.150277                 4.990769   
23                     1181                0.020459                 5.984748   
40                      799                0.118095                 4.960857   
42                     1395                0.177040                 4.790731   

    params_subsample     state  
34               NaN  COMPLETE  
37               NaN  COMPLETE  
23               NaN  COMPLETE  
40               NaN  COMPLETE  
42               NaN  COMPLETE

## **M1-Tunned Catboost Model**

In [ ]:
# Split train/test
X = train_or_prep[features]
y = train_or_prep['depression']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)

In [79]:
# Define multiple scoring metrics
scoring = {
    'AUC': 'roc_auc',
    'MCC': 'matthews_corrcoef',
    'ACC': 'accuracy'
}

# Run cross-validation once with multiple metrics
cv_results = cross_validate(
    CatBoostClassifier(**best_params, random_state=42, verbose=False),
    X_train,
    y_train,
    cv=5,
    scoring=scoring,
    fit_params={'cat_features': cat_features},
    n_jobs=-1,
    verbose=1
)

# Print results
for metric in scoring.keys():
    scores = cv_results[f'test_{metric}']
    print(f"{metric}: {scores.mean():.4f} ± {scores.std():.4f}")

AUC: 0.9759 ± 0.0013
MCC: 0.7652 ± 0.0072
ACC: 0.9180 ± 0.0025


In [80]:
# Train final model 
m1_model = CatBoostClassifier(**best_params, random_state=42)
m1_model.fit(X_train, y_train, cat_features=cat_features, verbose=False)

# Evaluate on validation set
val_preds = m1_model.predict_proba(X_test)[:, 1]
val_labels = (val_preds > 0.5).astype(int)

print("Validation Results:")
print(f"AUC: {roc_auc_score(y_test, val_preds):.4f}")
print(f"MCC: {matthews_corrcoef(y_test, val_labels):.4f}")
print(f"ACC: {accuracy_score(y_test, val_labels):.4f}")


Test Results:
AUC: 0.9750
MCC: 0.7661
ACC: 0.9185


## **M2-Tuned Bagged CatBoost Model**

I will produce a bagged Catboost model with the best parameters found by optuna. 

In [82]:
# Generate 10 Bagged Catboost models
m2_oof_preds, m2_models = train_bagged_model(
    X=X_train,
    y=y_train,
    model_params=best_params,
    n_folds=10,
    cat_features=cat_features
)

Training fold 1/10
Training fold 2/10
Training fold 3/10
Training fold 4/10
Training fold 5/10
Training fold 6/10
Training fold 7/10
Training fold 8/10
Training fold 9/10
Training fold 10/10

Overall CV Scores:
MCC Score: 0.7645
Accuracy Score: 0.9174
AUC Score: 0.9759

Cross-validation Scores (Mean ± Std):
MCC Score: 0.7645 ± 0.0066
Accuracy Score: 0.9174 ± 0.0028
AUC Score: 0.9759 ± 0.0013


In [95]:
# Generate validation set
validation = pd.concat([X_test, y_test], axis=1)

# Get predictions from each model in the ensemble and add as columns
for i, model in enumerate(m2_models):
    test_preds = model.predict_proba(X_test)[:, 1]
    validation[f'model_{i+1}_preds'] = test_preds

In [94]:
from scipy.stats import norm

def normalize_distributions(all_probs):
    normalized_probs = np.zeros_like(all_probs)
    
    for i in range(all_probs.shape[1]):
        # Convert to normal distribution
        probs = all_probs[:, i]
        normalized = norm.ppf(probs)
        # Back to [0,1] range
        normalized_probs[:, i] = norm.cdf(normalized)
    
    return normalized_probs

In [96]:
pred_cols = [pred_col for pred_col in validation.columns if 'model_' in pred_col]
validation[pred_cols] = normalize_distributions(validation[pred_cols].values)
validation['m2_bagged_preds'] = validation[pred_cols].mean(axis=1)

print("Validation Results:")
print(f"AUC: {roc_auc_score(y_test, validation['m2_bagged_preds']):.4f}")
print(f"MCC: {matthews_corrcoef(y_test, (validation['m2_bagged_preds'] > 0.5).astype(int)):.4f}")
print(f"ACC: {accuracy_score(y_test, (validation['m2_bagged_preds'] > 0.5).astype(int)):.4f}")

Validation Results:
AUC: 0.9751
MCC: 0.7659
ACC: 0.9182


In [97]:
# Convert each model's predictions to binary using 0.5 threshold
binary_pred_cols = []
for pred_col in pred_cols:
    binary_col = f'{pred_col}_binary'
    validation[binary_col] = (validation[pred_col] > 0.5).astype(int)
    binary_pred_cols.append(binary_col)

# Get majority vote prediction
validation['m2_vote_preds'] = (validation[binary_pred_cols].mean(axis=1) > 0.5).astype(int)

print("\nMajority Vote Results:")
print(f"AUC: {roc_auc_score(y_test, validation['m2_vote_preds']):.4f}")
print(f"MCC: {matthews_corrcoef(y_test, validation['m2_vote_preds']):.4f}") 
print(f"ACC: {accuracy_score(y_test, validation['m2_vote_preds']):.4f}")



Majority Vote Results:
AUC: 0.9232
MCC: 0.7663
ACC: 0.9185


In [98]:
validation

is_female  age         city  is_student      profession  \
id                                                                
75461           1   56        Patna           0       Architect   
56853           1   21      Kolkata           1         Missing   
131483          0   33      Kolkata           1         Missing   
139341          0   23  Vasai-Virar           0          Doctor   
79840           1   52     Ludhiana           0  Content Writer   
...           ...  ...          ...         ...             ...   
129971          1   43    Ahmedabad           0    Entrepreneur   
5024            1   31       Rajkot           0  Data Scientist   
48104           1   49        Patna           0  Content Writer   
69542           1   26         Pune           0         Teacher   
65039           0   33       Meerut           0         Missing   

        academic_pressure  work_pressure  cgpa  study_satisfaction  \
id                                                                   
75461                 NaN            3.0   NaN                 NaN   
56853                 5.0            NaN  7.21                 1.0   
131483                1.0            NaN  9.60                 4.0   
139341                NaN            3.0   NaN                 NaN   
79840                 NaN            1.0   NaN                 NaN   
...                   ...            ...   ...                 ...   
129971                NaN            5.0   NaN                 NaN   
5024                  NaN            3.0   NaN                 NaN   
48104                 NaN            5.0   NaN                 NaN   
69542                 NaN            3.0   NaN                 NaN   
65039                 NaN            5.0   NaN                 NaN   

        job_satisfaction  ... model_2_preds_binary model_3_preds_binary  \
id                        ...                                             
75461                1.0  ...                    0                    0   
56853                NaN  ...                    1                    1   
131483               NaN  ...                    0                    0   
139341               2.0  ...                    0                    0   
79840                4.0  ...                    0                    0   
...                  ...  ...                  ...                  ...   
129971               5.0  ...                    0                    0   
5024                 4.0  ...                    0                    0   
48104                3.0  ...                    0                    0   
69542                2.0  ...                    0                    0   
65039                1.0  ...                    1                    1   

       model_4_preds_binary  model_5_preds_binary  model_6_preds_binary  \
id                                                                        
75461                     0                     0                     0   
56853                     1                     1                     1   
131483                    0                     0                     0   
139341                    0                     0                     0   
79840                     0                     0                     0   
...                     ...                   ...                   ...   
129971                    0                     0                     0   
5024                      0                     0                     0   
48104                     0                     0                     0   
69542                     0                     0                     0   
65039                     1                     1                     1   

        model_7_preds_binary  model_8_preds_binary  model_9_preds_binary  \
id                                                                         
75461                      0                     0                     0   
56853                      1                 

# **Submission**

In [106]:
sub_m1_model = submission.copy()
sub_m1_model['Depression'] = m1_model.predict(test_prep)
sub_m1_model.to_csv('Data/submission_m1_model.csv', index=False)
sub_m1_model

id  Depression
0      140700           0
1      140701           0
2      140702           0
3      140703           1
4      140704           0
...       ...         ...
93795  234495           0
93796  234496           1
93797  234497           0
93798  234498           1
93799  234499           0

[93800 rows x 2 columns]

In [108]:
sub_m2_bagged_model = submission.copy()

# Get predictions from each model in the ensemble and add as columns
for i, model in enumerate(m2_models):
    test_preds = model.predict_proba(test_prep)[:, 1]
    sub_m2_bagged_model[f'model_{i+1}_preds'] = test_preds
    
pred_cols = [pred_col for pred_col in sub_m2_bagged_model.columns if 'model_' in pred_col]
sub_m2_bagged_model[pred_cols] = normalize_distributions(sub_m2_bagged_model[pred_cols].values)
sub_m2_bagged_model['m2_bagged_preds'] = sub_m2_bagged_model[pred_cols].mean(axis=1)
sub_m2_bagged_model['Depression'] = sub_m2_bagged_model['m2_bagged_preds']
sub_m2_bagged_model['Depression'] = (sub_m2_bagged_model['Depression'] > 0.5).astype(int)

sub_m2_bagged_model[['id', 'Depression']].to_csv('Data/submission_m2_bagged_model_normalized.csv', index=False)
sub_m2_bagged_model

id  Depression  model_1_preds  model_2_preds  model_3_preds  \
0      140700           0       0.000497       0.000601       0.000881   
1      140701           0       0.000332       0.000476       0.000476   
2      140702           0       0.096157       0.117643       0.111683   
3      140703           1       0.995707       0.994910       0.995121   
4      140704           0       0.083198       0.079060       0.083881   
...       ...         ...            ...            ...            ...   
93795  234495           0       0.005554       0.005210       0.006037   
93796  234496           1       0.980207       0.978174       0.977848   
93797  234497           0       0.068969       0.068245       0.062168   
93798  234498           1       0.966505       0.952425       0.965456   
93799  234499           0       0.030829       0.035505       0.028788   

       model_4_preds  model_5_preds  model_6_preds  model_7_preds  \
0           0.000524       0.000957       0.000574       0.000994   
1           0.000320       0.000454       0.000291       0.000482   
2           0.103428       0.110995       0.123894       0.104076   
3           0.996504       0.995151       0.995515       0.995461   
4           0.081392       0.077180       0.087347       0.076402   
...              ...            ...            ...            ...   
93795       0.005456       0.005259       0.004535       0.005751   
93796       0.979639       0.982249       0.979878       0.975504   
93797       0.067721       0.067573       0.068154       0.066505   
93798       0.959306       0.955151       0.957522       0.956142   
93799       0.028112       0.027762       0.027917       0.028659   

       model_8_preds  model_9_preds  model_10_preds  m2_bagged_preds  
0           0.000723       0.000598        0.000621         0.000697  
1           0.000392       0.000303        0.000422         0.000395  
2           0.114025       0.113579        0.088812         0.108429  
3           0.995084       0.994634        0.994955         0.995304  
4           0.071920       0.068837        0.064498         0.077372  
...              ...            ...             ...              ...  
93795       0.006153       0.005298        0.005074         0.005433  
93796       0.981100       0.976540        0.977754         0.978889  
93797       0.068832       0.072604        0.064617         0.067539  
93798       0.957702       0.955726        0.964668         0.959060  
93799       0.029186       0.028571        0.024369         0.028970  

[93800 rows x 13 columns]

In [109]:
sub_m2_bagged_model = submission.copy()

# Get predictions from each model in the ensemble and add as columns
for i, model in enumerate(m2_models):
    test_preds = model.predict_proba(test_prep)[:, 1]
    sub_m2_bagged_model[f'model_{i+1}_preds'] = test_preds
    
# Convert each model's predictions to binary using 0.5 threshold
binary_pred_cols = []
for pred_col in pred_cols:
    binary_col = f'{pred_col}_binary'
    sub_m2_bagged_model[binary_col] = (sub_m2_bagged_model[pred_col] > 0.5).astype(int)
    binary_pred_cols.append(binary_col)

# Get majority vote prediction
sub_m2_bagged_model['Depression'] = (sub_m2_bagged_model[binary_pred_cols].mean(axis=1) > 0.5).astype(int)
sub_m2_bagged_model[['id', 'Depression']].to_csv('Data/submission_m2_bagged_model_voting.csv', index=False)
sub_m2_bagged_model

id  Depression  model_1_preds  model_2_preds  model_3_preds  \
0      140700           0       0.000497       0.000601       0.000881   
1      140701           0       0.000332       0.000476       0.000476   
2      140702           0       0.096157       0.117643       0.111683   
3      140703           1       0.995707       0.994910       0.995121   
4      140704           0       0.083198       0.079060       0.083881   
...       ...         ...            ...            ...            ...   
93795  234495           0       0.005554       0.005210       0.006037   
93796  234496           1       0.980207       0.978174       0.977848   
93797  234497           0       0.068969       0.068245       0.062168   
93798  234498           1       0.966505       0.952425       0.965456   
93799  234499           0       0.030829       0.035505       0.028788   

       model_4_preds  model_5_preds  model_6_preds  model_7_preds  \
0           0.000524       0.000957       0.000574       0.000994   
1           0.000320       0.000454       0.000291       0.000482   
2           0.103428       0.110995       0.123894       0.104076   
3           0.996504       0.995151       0.995515       0.995461   
4           0.081392       0.077180       0.087347       0.076402   
...              ...            ...            ...            ...   
93795       0.005456       0.005259       0.004535       0.005751   
93796       0.979639       0.982249       0.979878       0.975504   
93797       0.067721       0.067573       0.068154       0.066505   
93798       0.959306       0.955151       0.957522       0.956142   
93799       0.028112       0.027762       0.027917       0.028659   

       model_8_preds  ...  model_1_preds_binary  model_2_preds_binary  \
0           0.000723  ...                     0                     0   
1           0.000392  ...                     0                     0   
2           0.114025  ...                     0                     0   
3           0.995084  ...                     1                     1   
4           0.071920  ...                     0                     0   
...              ...  ...                   ...                   ...   
93795       0.006153  ...                     0                     0   
93796       0.981100  ...                     1                     1   
93797       0.068832  ...                     0                     0   
93798       0.957702  ...                     1                     1   
93799       0.029186  ...                     0                     0   

       model_3_preds_binary  model_4_preds_binary  model_5_preds_binary  \
0                         0                     0                     0   
1                         0                     0                     0   
2                         0                     0                     0   
3                         1                     1                     1   
4                         0                     0                     0   
...                     ...                   ...                   ...   
93795                     0                     0                     0   
93796                     1                     1                     1   
93797                     0                     0                     0   
93798                     1                     1                     1   
93799                     0                     0                     0   

       model_6_preds_binary  model_7_preds_binary  model_8_preds_binary  \
0                         0                     0                     0   
1                         0                     0                     0   
2                         0                     0                     0   
3                         1                     1                     1   
4                         0                     0                     0   
...                     ...                   ...                